In [5]:
import random
from IPython.core.display import SVG
import pyomo.environ as pyo
from pysat.solvers import Solver
from pysat.formula import CNF 
import py_svg_combinatorics as psc
from ipywidgets import widgets, HBox
from collections import Counter
from pprint import pprint
from random import randint
import numpy as np
from IPython.display import IFrame
from IPython.display import display
import IPython
from copy import copy
import os
from pyomo_helpers import * 
import pandas
from pathlib import Path
from pyomo_helpers import pretty_solution
nbname = ''
try:
    nbname = __vsc_ipynb_file__
except:
    if 'COCALC_JUPYTER_FILENAME' in os.environ:
        nbname = os.environ['COCALC_JUPYTER_FILENAME']    
title_ = Path(nbname).stem.replace('-', '_').title()    
IFrame(f'https://discopal.ispras.ru/index.php?title=Hardprob/{title_}&useskin=cleanmonobook', width=1280, height=300)

In [6]:
d = 10
n = 5 # Number of vectors in X
M = 4

vectors = np.random.randint(0, 2, size=(d, n))

In [7]:
def visualize(vectors):
    df = pd.DataFrame(vectors, columns=["x" + str(i) for i in range(vectors.shape[1])])
    s = df.style.set_table_styles( [{'selector': 'td',
        'props': [
            ('border-left', '2px solid black !important'),
            ('border-right','2px solid black !important')
        ]}])
    return s
visualize(vectors)

In [8]:
def модель(вектора, M):
    m = pyo.ConcreteModel()
    m.множества = range(M)
    m.В = range(вектора.shape[1])
    m.D = range(вектора.shape[0])
    m.вектора = вектора
    m.X = pyo.Var(m.В, m.множества, domain=pyo.Binary)
    m.является_покрытием = pyo.Var(m.множества, domain=pyo.Binary) 
    
    @m.Objective(sense=pyo.maximize)
    def количество_покрытий(m, в):
        return sum(m.является_покрытием[...]) # важно указывать слайс при суммировании!
    
    @m.Constraint(m.В)
    def ровно_в_одном_множестве(m, в):
        return sum(m.X[в, ...]) == 1
    
    @m.Constraint(m.множества, m.D)
    def проверка_является_покрытием(m, мн, d):
        #Если хоть кто-то в мн 0 - то мн не покрытие
        return (m.вектора @ m.X)[d, мн] >= m.является_покрытием[мн]

    # @m.Constraint()
    # def wtf(m):
    #     return m.X[1,0]==1

    return m

In [9]:
m = модель(vectors, M)
m.pprint()



2 Var Declarations
    X : Size=20, Index={0, 1, 2, 3, 4}*{0, 1, 2, 3}
        Key    : Lower : Value : Upper : Fixed : Stale : Domain
        (0, 0) :     0 :  None :     1 : False :  True : Binary
        (0, 1) :     0 :  None :     1 : False :  True : Binary
        (0, 2) :     0 :  None :     1 : False :  True : Binary
        (0, 3) :     0 :  None :     1 : False :  True : Binary
        (1, 0) :     0 :  None :     1 : False :  True : Binary
        (1, 1) :     0 :  None :     1 : False :  True : Binary
        (1, 2) :     0 :  None :     1 : False :  True : Binary
        (1, 3) :     0 :  None :     1 : False :  True : Binary
        (2, 0) :     0 :  None :     1 : False :  True : Binary
        (2, 1) :     0 :  None :     1 : False :  True : Binary
        (2, 2) :     0 :  None :     1 : False :  True : Binary
        (2, 3) :     0 :  None :     1 : False :  True : Binary
        (3, 0) :     0 :  None :     1 : False :  True : Binary
        (3, 1) :     0 :  None : 

In [10]:
solver = pyo.SolverFactory('cbc')
# solver = pyo.SolverFactory('scip')
solver.solve(m).write()

# ==========================================================
# = Solver Results                                         =
# ==========================================================
# ----------------------------------------------------------
#   Problem Information
# ----------------------------------------------------------
Problem: 
- Name: unknown
  Lower bound: 1.0
  Upper bound: 1.0
  Number of objectives: 1
  Number of constraints: 36
  Number of variables: 23
  Number of binary variables: 24
  Number of integer variables: 24
  Number of nonzeros: 4
  Sense: maximize
# ----------------------------------------------------------
#   Solver Information
# ----------------------------------------------------------
Solver: 
- Status: ok
  User time: -1.0
  System time: 0.0
  Wallclock time: 0.01
  Termination condition: optimal
  Termination message: Model was solved to optimality (subject to tolerances), and an optimal solution is available.
  Statistics: 
    Branch and bound: 
   

In [11]:
def solve_d_vectors(vectors, M, solver_name='cbc'):
    m = модель(vectors, M)
    solver = pyo.SolverFactory(solver_name)
    solver.solve(m)
    cover = np.array([pyo.value(m.является_покрытием[i]) for i in range(M)])
    solution = np.array([[int(pyo.value(m.X[i, j])) for j in range(M)] for i in range(vectors.shape[1])])
    solution = solution[..., cover > 0]
    answer = m.количество_покрытий()
    return answer, solution

In [12]:
def visualize_solution(solution):
    df = pd.DataFrame(solution, columns=["s" + str(i) for i in range(solution.shape[1])], index=["x" + str(i)  for i in range(solution.shape[0])])
    return df.style.background_gradient()

In [13]:
visualize_solution(solve_d_vectors(vectors, M)[1])

## Сведение Sat к d-vector covering
### Идея

Подробнее посмотрим на условие, что k-е подмножество покрывает i-ю координату вектора: 
$\sum_{j}{V_{ij} S_{jk} > 0}$, 

где 
- $V$-матрица векторов, 
- $S$ - матрица множеств.


Или иначе $\lor_{j}{(V_{ij} = S_{jk} = 1)}$. Это дизъюнкция. 

Значит размерность `d` будет отвечать за число дизъюнкций в КНФ. 
А размерность `n` — число переменных в формуле. 

Рассмотрим на примере следующей КНФ: 

$(x1 \lor \overline{x2} \lor x3) \land (\overline{x1} \lor x2 \lor \overline{x4})$

|                                   closure| $x1$ | $\overline{x1}$ | $x2$ | $\overline{x2}$ | $x3$ | $\overline{x3}$ | $x4$ | $\overline{x4}$ |
|------------------------------------------|------|-----------------|------|-----------------|------|-----------------|------|-----------------|
|$x1 \lor \overline{x2} \lor x3$           | **1**|                0|     0|            **1**| **1**|                0|     0|                0|
|$\overline{x1} \lor x2 \lor \overline{x4}$|     0|            **1**| **1**|                0|     0|                0|     0|            **1**|

Тогда покрывающее множество векторов - решение КНФ

### Как не взять всё? 
В текущем подходе есть проблема - можно взять всё. Например одновременно переменную и её отрицание. 

Решение: будем разбивать переменные в два множества. Их условно можно назвать `True` и `False`. КНФ решаема тогда и только тогда когда все переменные можно непротиворечиво разбить на два этих множества.

Осталось только форсировать непротиворечивое разбиение. 
Для этого добавим тавтологические дизъюнкции в КНФ $xn \lor \overline{xn}$

|                                   closure| $x1$ | $\overline{x1}$ | $x2$ | $\overline{x2}$ | $x3$ | $\overline{x3}$ | $x4$ | $\overline{x4}$ |
|------------------------------------------|------|-----------------|------|-----------------|------|-----------------|------|-----------------|
|$x1 \lor \overline{x2} \lor x3$           | **1**|              0  |   0  |            **1**| **1**|              0  |   0  |              0  |
|$\overline{x1} \lor x2 \lor \overline{x4}$|   0  |            **1**| **1**|              0  |   0  |              0  |   0  |            **1**|
|                   $x1 \lor \overline{x1}$| **1**|            **1**|   0  |              0  |   0  |              0  |   0  |              0  |
|                   $x2 \lor \overline{x2}$|   0  |              0  | **1**|            **1**|   0  |              0  |   0  |              0  |
|                   $x3 \lor \overline{x3}$|   0  |              0  |   0  |              0  | **1**|            **1**|   0  |              0  |
|                   $x4 \lor \overline{x4}$|   0  |              0  |   0  |              0  |   0  |              0  | **1**|            **1**|

Теперь чтобы получить 2 покрывающих множества одно из них обязано содержать переменную а второе её отрицание. 

Если вдруг в одном множестве окажется и переменная и отрицание, то второе не сможет покрыть всё.

Например пусть разбиение следующее $\{x1, \overline{x1}, x2, x3, x4\}, \{\overline{x2}, \overline{x3}, \overline{x4}\}$

|                                   closure| $x1$ | $\overline{x1}$ | $x2$ | $x3$ | $x4$ |  sum|
|------------------------------------------|------|-----------------|------|------|------|  --:|
|$x1 \lor \overline{x2} \lor x3$           |   1  |              0  |   0  |   1  |   0  |**2**|
|$\overline{x1} \lor x2 \lor \overline{x4}$|   0  |              1  |   1  |   0  |   0  |**2**|
|                   $x1 \lor \overline{x1}$|   1  |              1  |   0  |   0  |   0  |**2**|
|                   $x2 \lor \overline{x2}$|   0  |              0  |   1  |   0  |   0  |**1**|
|                   $x3 \lor \overline{x3}$|   0  |              0  |   0  |   1  |   0  |**1**|
|                   $x4 \lor \overline{x4}$|   0  |              0  |   0  |   0  |   1  |**1**|


|                                   closure| $\overline{x2}$ | $\overline{x3}$ | $\overline{x4}$ |  sum|
|------------------------------------------|-----------------|-----------------|-----------------|  --:|
|$x1 \lor \overline{x2} \lor x3$           |            **1**|              0  |              0  |**1**|
|$\overline{x1} \lor x2 \lor \overline{x4}$|              0  |              0  |            **1**|**1**|
|                   $x1 \lor \overline{x1}$|              0  |              0  |              0  |**0**|
|                   $x2 \lor \overline{x2}$|            **1**|              0  |              0  |**1**|
|                   $x3 \lor \overline{x3}$|              0  |            **1**|              0  |**1**|
|                   $x4 \lor \overline{x4}$|              0  |              0  |            **1**|**1**|

Как видно, второе множество не является покрывающим

### Как найти второе решение
У текущего подхода есть ещё одна проблема. В общем случае неверно, что если $(x1, x2, \ldots)$ решение SAT то $(\overline{x1}, \overline{x2}, \ldots)$ тоже решение.
Но надо как то сделать так, чтобы отрицание было покрывающем множеством. Для этого введем новую переменную (назовем её $f$). И объявим её ложной. 

То есть сделаем ещё одно эквивалентное преобразование: $(x1 \lor \overline{x2} \lor x3) \Rightarrow (x1 \lor \overline{x2} \lor x3 \lor False) \Rightarrow (x1 \lor \overline{x2} \lor x3 \lor f)$ при $f = False$
Проделаем так с каждой **оригинальной** скобкой в КНФ: 


|                                   closure| $x1$ | $\overline{x1}$ | $x2$ | $\overline{x2}$ | $x3$ | $\overline{x3}$ | $x4$ | $\overline{x4}$ |   f |
|------------------------------------------|------|-----------------|------|-----------------|------|-----------------|------|-----------------|-----|
|$x1 \lor \overline{x2} \lor x3$           | **1**|              0  |   0  |            **1**| **1**|              0  |   0  |              0  |**1**|
|$\overline{x1} \lor x2 \lor \overline{x4}$|   0  |            **1**| **1**|              0  |   0  |              0  |   0  |            **1**|**1**|
|                   $x1 \lor \overline{x1}$| **1**|            **1**|   0  |              0  |   0  |              0  |   0  |              0  |  0  |
|                   $x2 \lor \overline{x2}$|   0  |              0  | **1**|            **1**|   0  |              0  |   0  |              0  |  0  |
|                   $x3 \lor \overline{x3}$|   0  |              0  |   0  |              0  | **1**|            **1**|   0  |              0  |  0  |
|                   $x4 \lor \overline{x4}$|   0  |              0  |   0  |              0  |   0  |              0  | **1**|            **1**|  0  |

### Итого: 
- Если нашлось разбиение на 2 множества, то ни одно из них не содержит одновременно переменную и её отрицание
- Множество не содержащее $f$ является решением КНФ.

In [14]:
cnf_vars = 5
cnf_clauses = 20

cnf3 = CNF(from_clauses=psc.rand3cnf(cnf_clauses, cnf_vars))
clauses = cnf3.clauses

In [15]:
def solve_sat(cnf_vars, cnf_clauses, clauses):
    vectors = np.zeros((cnf_clauses + cnf_vars, 2*cnf_vars + 1))
    for i in range(cnf_clauses):
        for j in clauses[i]:
            vectors[i][j + cnf_vars] = 1
        vectors[i][cnf_vars] = 1 # Contradict

    for i in range(1, cnf_vars+1):
        vectors[cnf_clauses + i - 1][cnf_vars - i] = 1
        vectors[cnf_clauses + i - 1][cnf_vars + i] = 1 
    sol = solve_d_vectors(vectors, 2)
    return sol[0] == 2

In [16]:
solve_sat(cnf_vars, cnf_clauses, clauses)

True

In [17]:
cnf_vars = 5
cnf_clauses = 1

cnf3 = CNF(from_clauses=psc.rand3cnf(cnf_clauses, cnf_vars))
clauses = cnf3.clauses

In [18]:
clauses

[[-3, 2, 1]]

In [19]:
solve_sat(cnf_vars, cnf_clauses, clauses)

True

In [20]:
def test_sat_iter(N, cnf_vars, cnf_clauses):
    mistakes = 0
    for _ in range(N):
        cnf3 = CNF(from_clauses=psc.rand3cnf(cnf_clauses, cnf_vars))
        clauses = cnf3.clauses
        sol_this = solve_sat(cnf_vars, cnf_clauses, clauses)
        py3sat_test_solver = Solver(bootstrap_with=cnf3)
        sol_other = py3sat_test_solver.solve()
        if sol_this != sol_other:
            mistakes += 1
    return mistakes

In [21]:
def stress_test():
    for i in range(100):
        if test_sat_iter(20, 4, 20) > 5:
            print("Failed")
            return
        if i % 10 == 0:
            print("Passed ", i)

In [22]:
stress_test()

Passed  0
Passed  10
Passed  20
Passed  30
Passed  40
Passed  50
Passed  60
Passed  70
Passed  80
Passed  90
